In [33]:
import pandas as pd

In [34]:
# Importacion de Plotly como libreria de DataViz
import plotly.express as px
import plotly.graph_objects as go
import plotly.figure_factory as ff

In [35]:
import os

# Obtiene la ubicación completa del archivo del notebook
notebook_path = os.path.realpath('__file__')

# Obtiene la ruta absoluta de la carpeta "Coderhouser-DS-TP0002" sin importar donde te encuentres
path_base = os.path.abspath(os.path.join(notebook_path, "..", "..", "..", "Coderhouser-DS-TP0002"))

print("Path base':", path_base)

Path base': C:\develoment\Coderhouser-DS-TP0002


#### Leyendo datos:

In [42]:
# Generando el Dataframe apartir de los dataset RedTeam y BlueTeam
blueTeam = pd.read_csv( path_base + r"\\data\procesed\blueTeam.csv")
blueTeam["Team"] = "Blue"
redTeam = pd.read_csv( path_base + r"\\data\procesed\redTeam.csv")
redTeam["Team"] = "Red"
data = pd.concat([blueTeam,redTeam])

In [43]:
# Reemplazar los valores de la columna "Wins"
data['WinTags'] = data['Wins'].replace({0: 'Loss', 1: 'Win'})

# Crear un mapeo de colores
color_map = {'Win': 'yellow', 'Loss': 'gray'}

In [45]:
data.drop(columns=["Unnamed: 0"], inplace=True)

In [46]:
# Detalle de tabla
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 19758 entries, 0 to 9878
Data columns (total 22 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   Wins                      19758 non-null  int64  
 1   WardsPlaced               19758 non-null  int64  
 2   WardsDestroyed            19758 non-null  int64  
 3   FirstBlood                19758 non-null  int64  
 4   Kills                     19758 non-null  int64  
 5   Deaths                    19758 non-null  int64  
 6   Assists                   19758 non-null  int64  
 7   EliteMonsters             19758 non-null  int64  
 8   Dragons                   19758 non-null  int64  
 9   Heralds                   19758 non-null  int64  
 10  TowersDestroyed           19758 non-null  int64  
 11  TotalGold                 19758 non-null  int64  
 12  AvgLevel                  19758 non-null  float64
 13  TotalExperience           19758 non-null  int64  
 14  TotalMi

### Hipotesis
Estas hipótesis proporcionan una base sólida para realizar pruebas y análisis más detallados sobre el dataset de League of Legends. Al evaluar cada una de estas hipótesis y validarlas con datos, el equipo podrá obtener una mejor comprensión de los factores que realmente influyen en el rendimiento y la probabilidad de victoria en el juego.

- **Hipótesis 1**: Control temprano del mapa y victoria Equipos que logran un mayor control del mapa mediante la colocación de más "Warding totems" en áreas estratégicas durante los primeros 10 minutos tendrán una mayor probabilidad de ganar la partida.

- **Hipótesis 1**: Relación entre asesinatos y tasa de victoria El número de asesinatos conseguidos por un equipo en los primeros 10 minutos se correlacionará positivamente con su tasa de victoria. Cuanto mayor sea la cantidad de asesinatos, más alta será la probabilidad de ganar.

In [51]:
# Crear un histograma combinado
fig = px.histogram(data, x='Kills', color='WinTags', 
                   color_discrete_map=color_map, marginal="box", 
                   title="Histograma de Asesinatos en Partidas Ganadas y Perdidas")
fig.update_layout(xaxis_title="Número de Asesinatos", yaxis_title="Cantidad de Partidas")

# Mostrar el gráfico
fig.show()
fig.write_html(path_base + r"\\static\html\Hypothesis_001.html")
fig.write_image(path_base + r"\\static\img\Hypothesis_001.png")

- **Hipótesis 2**: Impacto de objetivos neutrales en la victoria Equipos que aseguran más dragones y Herald durante los primeros 10 minutos tendrán una mayor probabilidad de ganar la partida, ya que estos objetivos proporcionan beneficios significativos para todo el equipo.

In [ ]:
pd.concat([data.loc[data["Dragons"]==1][["TotalExperience","TotalGold"]].describe(),
            data.loc[data["Dragons"]==0][["TotalExperience","TotalGold"]].describe()],axis=1)

In [74]:
pd.concat([data.loc[data["Heralds"]==1][["TotalExperience","TotalGold"]].describe(),
            data.loc[data["Heralds"]==0][["TotalExperience","TotalGold"]].describe()],axis=1)

TotalExperience     TotalGold  TotalExperience     TotalGold
count      3438.000000   3438.000000     16320.000000  16320.000000
mean      18328.270797  17000.586387     17864.162990  16390.003738
std        1127.617683   1561.164025      1198.769624   1481.346367
min       13988.000000  12937.000000     10098.000000  10730.000000
25%       17570.750000  15889.000000     17101.000000  15342.000000
50%       18330.000000  16898.000000     17888.000000  16282.000000
75%       19111.000000  17991.750000     18660.000000  17318.000000
max       22269.000000  23701.000000     22258.000000  23424.000000

In [60]:
# Crear un Scatter combinado
fig = px.scatter(data, x="TotalExperience", y="TotalGold", 
                color='WinTags', color_discrete_map=color_map, 
                facet_row="Dragons", marginal_y="box",
                title="Correlación entre Dragon y Experiencia vs Oro")

# Mostrar el gráfico
fig.show()
fig.write_html(path_base + r"\\static\html\Hypothesis_002A.html")
fig.write_image(path_base + r"\\static\img\Hypothesis_002A.png")

In [61]:
# Crear un Scatter combinado
fig = px.scatter(data, x="TotalExperience", y="TotalGold", 
                color='WinTags', color_discrete_map=color_map, 
                facet_row="Heralds", marginal_y="box",
                title="Correlación entre Herald y Experiencia vs Oro")

# Mostrar el gráfico
fig.show()
fig.write_html(path_base + r"\\static\html\Hypothesis_002B.html")
fig.write_image(path_base + r"\\static\img\Hypothesis_002B.png")

In [69]:
# Crear un gráfico de heatmap para mostrar la relación
fig = px.density_heatmap(data.loc[data["WinTags"]=="Win"], x='Dragons', y='Heralds', text_auto=True,
                         title="Relación entre Captura de Dragones, Herald y Resultado")

# Personalizar el gráfico
fig.update_layout(
    xaxis_title="Cantidad de Dragones",
    yaxis_title="Cantidad de Heralds",
    coloraxis_colorbar_title="Resultado",
)

# Mostrar el gráfico
fig.show()
fig.write_html(path_base + r"\\static\html\Hypothesis_002.html")
fig.write_image(path_base + r"\\static\img\Hypothesis_002.png")

In [68]:
h1d1 = 1043
h1d0 = 1030
h0d1 = 3803
h0d0 = 4003

suma = h1d1+h1d0+h0d1+h0d0
print("evaluacion:")
print("no dragon y no herald:", round(h0d0/suma,4))
print("si dragon y no herald:", round(h0d1/suma,4))
print("no dragon y si herald:", round(h1d0/suma,4))
print("si dragon y si herald:", round(h1d1/suma,4))


evaluacion:
no dragon y no herald: 0.4052
si dragon y no herald: 0.385
no dragon y si herald: 0.1043
si dragon y si herald: 0.1056


- **Hipótesis 3**: Importancia de la ventaja económica y de experiencia Equipos que logran una ventaja significativa en oro y experiencia sobre el equipo contrario en los primeros 10 minutos tendrán mayores posibilidades de obtener la victoria.


In [78]:
# Crear un gráfico de dispersión para analizar la ventaja económica vs. experiencia
fig = px.scatter(data, x='GoldDiff', y='ExperienceDiff', 
                 color='WinTags', color_discrete_map=color_map, 
                 title="Ventaja Económica vs. Ventaja de Experiencia y Resultado")

# Personalizar el gráfico
fig.update_layout(
    xaxis_title="Diferencia de Oro (GoldDiff)",
    yaxis_title="Diferencia de Experiencia (ExperienceDiff)",
    coloraxis_colorbar_title="Resultado",
)

# Mostrar el gráfico
fig.show()
fig.write_html(path_base + r"\\static\html\Hypothesis_003.html")
fig.write_image(path_base + r"\\static\img\Hypothesis_003.png")

In [79]:
pd.concat([data.loc[data["WinTags"]=="Win"][["GoldDiff","ExperienceDiff"]].describe(),
            data.loc[data["WinTags"]=="Loss"][["GoldDiff","ExperienceDiff"]].describe()],axis=1)

GoldDiff  ExperienceDiff      GoldDiff  ExperienceDiff
count   9879.000000     9879.000000   9879.000000     9879.000000
mean    1253.860006      940.147889  -1253.860006     -940.147889
std     2108.745103     1674.809101   2108.745103     1674.809101
min    -6744.000000    -5355.000000 -11467.000000    -9333.000000
25%     -154.000000     -182.000000  -2574.000000    -2012.500000
50%     1182.000000      899.000000  -1182.000000     -899.000000
75%     2574.000000     2012.500000    154.000000      182.000000
max    11467.000000     9333.000000   6744.000000     5355.000000

- **Hipótesis 4**: Contribución individual y tasa de victoria Jugadores que contribuyen con un mayor número de asistencias tendrán un impacto positivo en la tasa de victoria de su equipo en las partidas clasificatorias Diamante.

In [82]:
# Crear un gráfico de barras para analizar la contribución individual (asistencias) y la tasa de victoria
fig = px.histogram(data, x='Assists', y='WinTags', orientation='h',
             title="Contribución Individual (Asistencias) vs. Tasa de Victoria")

# Personalizar el gráfico
fig.update_layout(
    xaxis_title="Número de Asistencias",
    yaxis_title="Resultado",
    showlegend=False,  # Para ocultar la leyenda
)

# Mostrar el gráfico
fig.show()
fig.write_html(path_base + r"\\static\html\Hypothesis_004.html")
fig.write_image(path_base + r"\\static\img\Hypothesis_004.png")

- **Hipótesis 5**: Nivel promedio y probabilidad de victoria Un equipo con un mayor nivel promedio de sus jugadores durante los primeros 10 minutos tendrá una mayor probabilidad de ganar la partida.

In [85]:
# Crear un gráfico de barras para analizar el nivel promedio y la tasa de victoria
fig = px.histogram(data, x='AvgLevel', y='WinTags',
             title="Nivel Promedio vs. Tasa de Victoria")

# Personalizar el gráfico
fig.update_layout(
    xaxis_title="Nivel Promedio",
    yaxis_title="Resultado",
    showlegend=False,  # Para ocultar la leyenda
)

# Mostrar el gráfico
fig.show()
fig.write_html(path_base + r"\\static\html\Hypothesis_005.html")
fig.write_image(path_base + r"\\static\img\Hypothesis_005.png")